In [1]:
import openai
import yaml
import os

import pandas as pd
import numpy as np
import json

# set up GPT

In [2]:
# Use absolute path to the config.yaml file
config_path = "C:/Users/Ryo/OneDrive/Desktop/LLMs/gpt_config.yaml"

In [3]:
with open(config_path) as f:
    config_yaml = yaml.load(f, Loader=yaml.FullLoader)
api_key = config_yaml['token']

client = openai.OpenAI(
    api_key = api_key
)

In [4]:
# select model
# gpt-3.5-turbo-0125 OR gpt-4o-2024-05-13
model = "gpt-4o-2024-05-13"

# prepare text data

In [5]:
# Load the Excel file
file_path = "C:/Users/Ryo/OneDrive/Desktop/Master Thesis/study/study1/raw/sample_forFeeding.xlsx"

text_set = pd.read_excel(file_path, sheet_name='text_only') 
sample_set = pd.read_excel(file_path, sheet_name='sample')

In [6]:
text_set.head()

posts_filtered
0  'OP, do you use psychotropic medication, like ...
1  'That is why I LOVE the Disney film Enchanted....
2  'I love malapropisms. Carmine 'Little Carmine'...
3  'I often listen to music that mirrors my mood....
4  'Please ignore this post. I just misread someo...

In [7]:
sample_set

1st choice 2nd choice 3rd choice  \
0       ENTP       ENFP       INTP   
1       INFP       ISFP       INFJ   
2       ENTP       ENTJ       INTJ   

                   Justification for 1st choice (EI)  \
0  Displays a range of interests and adaptability...   
1  Reflects introspection and a preference for so...   
2  Engages in diverse discussions, suggesting ext...   

                   Justification for 1st choice (NS)  \
0  Shows a preference for exploring abstract idea...   
1  Emphasizes emotional depth and abstract expres...   
2  Prefers theoretical and abstract discussions, ...   

                   Justification for 1st choice (TF)  \
0  Focuses on logical analysis but also values em...   
1  Prioritizes personal values and emotional unde...   
2  Analytical and objective in decision-making, a...   

                   Justification for 1st choice (PJ)  
0  Demonstrates flexibility and spontaneity, char...  
1  Shows a contemplative and open-ended approach ...  
2  Adaptable and open to new ideas, traits of per...

# feed into gpt

In [8]:
keys_list = ['1st choice',	'2nd choice',	'3rd choice',	'Justification for 1st choice (EI)',	'Justification for 1st choice (NS)',	'Justification for 1st choice (TF)',	'Justification for 1st choice (PJ)']

## activate a following cell to conduct a pilot test

In [9]:
tmp_df = text_set.head(10)
tmp_df

posts_filtered
0  'OP, do you use psychotropic medication, like ...
1  'That is why I LOVE the Disney film Enchanted....
2  'I love malapropisms. Carmine 'Little Carmine'...
3  'I often listen to music that mirrors my mood....
4  'Please ignore this post. I just misread someo...
5  'I've never come across an {MBTI type} IRL, so...
6  I can relate to almost all of what was said, y...
7  'I've given everyone I know a good reason to g...
8  'Moving on sucks, I find it helpful to keep ac...
9  'Hahaha! I was watching it too! What did you f...

## a full commit

In [10]:
# pilot
#target_df = tmp_df
# a full commit
target_df = text_set

In [11]:
results = []

for index, row in target_df.iterrows():
    print(row['posts_filtered'])
    prompt = f"Analyze the given one group of quotes containing multiple posts from the same speaker (each post is splitted using the symbol '|||') and classify him/her according to the Myers-Briggs Personality Indicator (MBTI).  Provide the top three MBTI predictions with justifications only for the first choice focusing on the four core aspects of MBTI: Extraversion vs. Introversion (E vs I), Sensing vs. Intuition (S vs N), Thinking vs. Feeling (T vs F), and Judging vs. Perceiving (J vs P). Make sure your response is in json format ready to be read using json.loads() method properly and follows the template in {sample_set}. Make sure your output contains all keys from {keys_list} and your answers corresponding to each of the keys.  Do not add any additional text in your response. Here's set of quotes {row['posts_filtered']}"
    response = client.chat.completions.create(
        model=model,
        messages=[{"role": "system", "content": "You are a helpful assistant."},
                  {"role": "user", "content": prompt}],
        temperature=1.0,
        max_tokens=500,
        top_p=1.0
    )
    output = response.choices[0].message.content
    print(output)
    try:
        json_data = output.strip('```json\n```')
        try:
            data = json.loads(json_data)
        except json.JSONDecodeError:
            json_data = output.strip('```json\n```  ')
            data = json.loads(json_data)
        results.append(data)
    except json.JSONDecodeError as e:
        print(f"Failed to decode JSON: {e}")
        print("Faulty JSON data:", json_data)  # This will show the problematic part.
        fallback_data = {
            "1st choice": "na",
            "2nd choice": "na",
            "3rd choice": "na",
            "Justification for 1st choice (EI)": "na",
            "Justification for 1st choice (NS)": "na",
            "Justification for 1st choice (TF)": "na",
            "Justification for 1st choice (PJ)": "na"
        }
        results.append(fallback_data)

# Convert results to DataFrame
output_df = pd.DataFrame(results)

output_df.tail(10)

'OP, do you use psychotropic medication, like antidepressants for example? They sometimes have a very hard effect on your libido. This would explain that.  If not, do you take in other kind of...|||I'm fantasmagorically attracted to what I see as the {MBTI type} archetype, but I think it would be extremely difficult to have a healthy and durable relationship (even a simple friendship) with an {MBTI type}....|||I'm done talking with  drmiller100 ; I don't have so much time to lose. Have fun trolling other people.  Sorry for poluting your thread, philosopherspidy .|||Are you really trying to understand what I mean? I think you're just trying to upset me. If you're not, you're extremely disrespectful to me anyway. And you feel proud, really?..  Anyway, you're...|||Aren't {MBTI type} famous for being great scientists, too? I wasn't talking about a law as in you shouldn't do that, it's wrong. It was a law as in at most one line can be drawn through any point not on...|||Just to clarify, I d

1st choice 2nd choice 3rd choice  \
614       ENFP       INFP       ESFP   
615       ENFJ       ENTP       ENFP   
616       ENFP       ESFJ       ENFJ   
617       ENTP       ENFP       INTP   
618       ENFP       INFJ       ENFJ   
619       INFP       INFJ       ISFP   
620       INFP       ISFP       INFJ   
621       INFP       ISFP       INFJ   
622       INFJ       INFP       ISFJ   
623       INFJ       INFP       ENFJ   

                     Justification for 1st choice (EI)  \
614  The speaker exhibits a high level of engagemen...   
615  Displays a preference for engaging with others...   
616  Displays sociable and engaging behavior, frequ...   
617  Engages in multiple discussions, plays with id...   
618  Displays a preference for engaging with others...   
619  Reflects introspection and a preference for so...   
620  Reflects introspection and a preference for so...   
621  Reflects introspection and a preference for so...   
622  Reflects introspection and a preference for so...   
623  Reflects introspection and a preference for so...   

                     Justification for 1st choice (NS)  \
614  There is a strong focus on abstract ideas, pos...   
615  Shows interest in abstract concepts like MBTI ...   
616  Shows interest in abstract concepts like MBTI ...   
617  Shows a preference for exploring abstract idea...   
618  The speaker frequently discusses abstract idea...   
619  Emphasizes abstract ideas, theoretical concept...   
620  Emphasizes emotional depth and abstract expres...   
621  Emphasizes emotional depth and abstract expres...   
622  Emphasizes emotional depth, abstract expressio...   
623  Displays a deep focus on cognitive functions a...   

                     Justification for 1st choice (TF)  \
614  The speaker often discusses feelings, values, ...   
615  Focuses on emotional connections, empathy, and...   
616  Often discusses feelings and values, both pers...   
617  Focuses on logical analysis and enjoys debatin...   
618  The speaker often expresses emotions and perso...   
619  Prioritizes personal values and emotional unde...   
620  Prioritizes personal values and emotional unde...   
621  Prioritizes personal values and emotional unde...   
622  Shows a combination of empathy, personal value...   
623  Emphasizes personal values and emotional under...   

                     Justification for 1st choice (PJ)  
614  The speaker shows flexibility, spontaneity, an...  
615  Demonstrates an organized and planned approach...  
616  Mentions spontaneity and flexibility in behavi...  
617  Demonstrates flexibility, spontaneity, and ada...  
618  Demonstrates an openness to new experiences an...  
619  Shows a contemplative and open-ended approach,...  
620  Shows a contemplative and open-ended approach ...  
621  Shows a contemplative and open-ended approach ...  
622  Displays a structured approach to dealing with...  
623  Shows a tendency towards structured and planne...

In [12]:
# Save to Excel
# gpt-4o
output_df.to_excel("C:/Users/Ryo/OneDrive/Desktop/Master Thesis/study/study1/raw/gpt4o_result_raw.xlsx", index=False)
# gpt-3.5
#output_df.to_excel("C:/Users/Ryo/OneDrive/Desktop/Master Thesis/study/study1/raw/gpt35_result_raw.xlsx", index=False)